In [1]:
%cd E:\try

E:\try


In [2]:
import tensorflow as tf
import PIL
from tensorflow.keras.models import Model
from tensorflow.keras.layers import (Dropout, Dense, Softmax)
from tensorflow.keras.applications import mobilenet as _mobilenet
import random
import os
import numpy as np
from moviepy.editor import VideoFileClip

from PIL import Image

In [3]:
def load_image(img_file, target_size=(224,224)):
    X = np.zeros((1, *target_size, 3))
    X[0, ] = np.asarray(tf.keras.preprocessing.image.load_img(
        img_file, 
        target_size=target_size)
    )
    X = tf.keras.applications.mobilenet.preprocess_input(X)
    return X


def ensure_folder_exists(folder):
    if not os.path.exists(folder):
        os.makedirs(folder)


model = tf.keras.applications.mobilenet.MobileNet(
# The 3 is the three dimensions of the input: r,g,b.
  input_shape=(224, 224, 3), 
  include_top=False, 
  pooling='avg'
)


In [4]:
model.save_weights(r'E:\try\my_checkpoint')
model.load_weights(r'E:\try\my_checkpoint')

In [5]:
def process_all_films(folder_path, interval, model):
    film_features = []
    ensure_folder_exists('../Frames/')

    for file in os.listdir(folder_path):
        try:
            if file.endswith(".mp4"): 
                film_path = os.path.join(folder_path, file)
                features = processFilmByFrames(file, film_path, interval, model)
                film_features.extend(features)
        except Exception as e:
            print(f"Error processing {file}: {e}")
    
    return film_features

def processFilmByFrames(filmName, filmPath, interval, model):
    features = []
    film = VideoFileClip(filmPath)
    nrFrames = int(film.duration / interval)

    for i in range(nrFrames):
        s = i * interval
        frame = film.get_frame(s)
        frame_image = Image.fromarray(frame, 'RGB')
        temp_frame_path = f'../Frames/{filmName}_{i}.jpg'
        frame_image.save(temp_frame_path)
        
        im = load_image(temp_frame_path)
        f = model.predict(im)[0]
        features.append({'film': filmPath, 'second': s, 'features': f})

        # Optional: Remove the temp image after processing
        os.remove(temp_frame_path)

    return features

In [6]:
def processImage(imagePath, model):
    im = load_image(imagePath)
    f = model.predict(im)[0]
    return f


In [7]:
import heapq

def findTopFramesByImage(filmFeatures, imagePath, model, top_n=9):
    imF = processImage(imagePath, model)
    
    top_frames_heap = []

    for index, f in enumerate(filmFeatures):
        dist = np.linalg.norm(f['features'] - imF)

        # Using a tuple of (negative distance, index) to maintain a max heap
        if len(top_frames_heap) < top_n:
            heapq.heappush(top_frames_heap, (-dist, index))
        else:
            heapq.heappushpop(top_frames_heap, (-dist, index))

    # Convert heap to sorted list (from closest to farthest)
    top_frames_sorted = sorted(top_frames_heap, key=lambda x: x[0], reverse=True)

    # Extracting the film and second information for the top frames
    return [filmFeatures[idx] for _, idx in top_frames_sorted]

In [8]:
def getFilmAroundFrame(frameInfo, radius):
    film = VideoFileClip(frameInfo[0])
    s = max(frameInfo[-1] - radius, 0)
    e = min(frameInfo[-1]+radius, film.duration)
    return film.subclip(s,e)

In [9]:
film_features = process_all_films(r'E:\try\ScrapedVideos', 10, model)

1/1 [==============================] - 0s 32ms/step


1/1 [==============================] - 0s 27ms/step


1/1 [==============================] - 0s 31ms/step


1/1 [==============================] - 0s 31ms/step


1/1 [==============================] - 0s 31ms/step


...

1/1 [==============================] - 0s 313ms/step


1/1 [==============================] - 0s 298ms/step


1/1 [==============================] - 0s 295ms/step


1/1 [==============================] - 0s 285ms/step


1/1 [==============================] - 0s 290ms/step


In [10]:
film_features[0]

{'film': 'E:\\try\\ScrapedVideos\\10_11KitchenMetaStories.mp4',
 'second': 0,
 'features': array([0., 0., 0., ..., 0., 0., 0.], dtype=float32)}

In [29]:
top_matches = findTopFramesByImage(film_features, r'C:\Users\SherryAi\Desktop\books\medieval\process\RIdeath.webp', model, top_n=50)

1/1 [==============================] - 0s 248ms/step


In [30]:
top_matches

[{'film': 'E:\\try\\ScrapedVideos\\Bekcett-Samuel_Silence-to-Silence_Documentary_1991.mp4',
  'second': 3730,
  'features': array([0.31513575, 0.16906637, 1.5839425 , ..., 0.7538899 , 0.        ,
         0.24551423], dtype=float32)},
 {'film': 'E:\\try\\ScrapedVideos\\Bekcett-Samuel_Silence-to-Silence_Documentary_1991.mp4',
  'second': 4190,
  'features': array([1.5073649 , 0.49015722, 0.9770839 , ..., 0.60976   , 0.06117237,
         0.6140053 ], dtype=float32)},
 {'film': 'E:\\try\\ScrapedVideos\\Bekcett-Samuel_Silence-to-Silence_Documentary_1991.mp4',
  'second': 3680,
  'features': array([1.8934103 , 0.33995792, 0.32622683, ..., 0.40601057, 0.3360795 ,
         0.3710292 ], dtype=float32)},
 {'film': 'E:\\try\\ScrapedVideos\\Bailey-Derek_On-the-Edge_Part-3.mp4',
  'second': 2940,
  'features': array([0.6434123 , 0.03156934, 1.4664468 , ..., 1.3277211 , 0.11617769,
         0.66966677], dtype=float32)},
 {'film': 'E:\\try\\ScrapedVideos\\Bekcett-Samuel_Silence-to-Silence_Documentar

In [ ]:
import os

# Create the output directory if it doesn't exist
output_directory = r'E:\try\output\death'
os.makedirs(output_directory, exist_ok=True)

frameClips = []

# Assuming frame_info is a dictionary with 'film' and 'second' keys
for frame_info in top_matches:
    clip = getFilmAroundFrame((frame_info['film'], frame_info['second']), 2)
    frameClips.append(clip)

for index, clip in enumerate(frameClips):
    output_path = os.path.join(output_directory, f"{index}.mp4")
    clip.write_videofile(output_path, audio_codec='aac')




In [21]:
from moviepy.editor import VideoFileClip, clips_array

# Assuming this is your original folder path
folder_path = r'E:\try\king_c'

# List of your video file paths (adjust these paths as needed)
video_paths = [f'{folder_path}/0.mp4', f'{folder_path}/1.mp4',  
               f'{folder_path}/6.mp4', f'{folder_path}/7.mp4',]

# Load the videos and resize them
clips = [VideoFileClip(video).resize(width=480, height=270) for video in video_paths]

# Create a 3x3 grid
grid = clips_array([[clips[0], clips[1]],
                    [clips[2], clips[3]]])

# Write the result to a file in the original folder
output_video_path = f'{folder_path}/four_panel_grid.mp4'
grid.write_videofile(output_video_path, fps=24)


Moviepy - Building video E:\try\king_c/four_panel_grid.mp4.
MoviePy - Writing audio in four_panel_gridTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video E:\try\king_c/four_panel_grid.mp4



Moviepy - Done !
Moviepy - video ready E:\try\king_c/four_panel_grid.mp4


In [51]:
from IPython.display import Video

# Path to your nine-panel grid video
video_file_path = r'E:\try\honor\nine_panel_grid.mp4'  # Use raw string for file path

# Display the video
Video(video_file_path, embed=True)

